# ÁNH XẠ DỮ LIỆU VÀO ĐỒ THỊ OPENSTREETMAP

## TRUY CẬP DỮ LIỆU VÀ KHỞI TẠO CÁC HÀM

In [1]:
import pandas as pd
import numpy as np
import folium
import matplotlib.pyplot as plt
import math
# from sklearn.cluster import DBSCAN
from apyori import apriori
import warnings
warnings.filterwarnings("ignore")

In [2]:
df = pd.read_csv("data_pre.csv")

In [5]:
len(list(df['vehicle'].unique()))

5856

In [6]:
df["vehicle"].value_counts()

51F33308     494
51G48323     472
51G50101     438
51C31679     404
51F85909     400
            ... 
51B18551       5
80M00242       5
51C57019       4
51C59948       3
50LD00479      3
Name: vehicle, Length: 5856, dtype: int64

In [7]:
def Distance(p1, p2):

    # GEPoint2D p1, GEPoint2D p2

    if p1.x == p2.x and p1.y == p2.y:
        return 0

    dbLat1InRad = p1.y * (math.pi / 180.0)
    dbLong1InRad = p1.x * (math.pi / 180.0)
    dbLat2InRad = p2.y * (math.pi / 180.0)
    dbLong2InRad = p2.x * (math.pi / 180.0)

    dbTheta = p1.x - p2.x
    dbThetaInRad = dbTheta * (math.pi / 180.0)

    a = math.sin(dbLat1InRad)
    b = math.sin(dbLat2InRad)
    c = math.cos(dbLat1InRad)
    d = math.cos(dbLat2InRad)
    e = math.cos(dbThetaInRad)
    f = a * b + c * d * e

    if f > 1:
        f = 1
    if f < -1:
        f = -1

    dbDistInRad = math.acos(f)
    dbDist = dbDistInRad * 180.0 / math.pi
    dbDist = dbDist * 60.0 * 1.1515
    dbDist = dbDist * 1.609344 * 1000

    return dbDist

In [8]:
def add_markers(gdf):
    f = folium.Figure(height = 800)
    mapobj = folium.Map([np.median(gdf.lat), np.median(gdf.lon)], zoom_start = 15, tiles='Cartodb dark_matter')
    mapobj.add_to(f)
    coords = []
    for i, row in gdf.iterrows():
        coords.append([row.lat, row.lon])
    for coord in coords:
        folium.CircleMarker(location = coord,
                            radius = 2.5, 
                            fill = True,
                            fill_color = '#F50057',
                            fill_opacity = 0.75,
                            color = 'whitesmoke',
                            weight = 0.5).add_to(mapobj)
    return mapobj

In [20]:
df_vehicle_count = pd.DataFrame(df["vehicle"].value_counts())
df_vehicle_count = df_vehicle_count.reset_index()
df_vehicle_count.rename(columns = {'index':'name'})
df_vehicle_count['id'] = df_vehicle_count.index

In [10]:
dict_id = pd.Series(df_vehicle_count.id.values,index=df_vehicle_count['index']).to_dict()

In [11]:
df['id_color'] = df.apply(lambda row: dict_id[row.vehicle], axis = 1)

In [12]:
df

vehicle  level_1             datetime  speed           y          x  \
0       14B02190        0  2018-04-24 22:39:49   14.0  106.697784  10.786592   
1       14B02190        1  2018-04-24 22:40:09    5.0  106.697710  10.786522   
2       14B02190        2  2018-04-24 22:40:19   24.0  106.697296  10.786112   
3       14B02190        3  2018-04-24 22:40:49   24.0  106.696610  10.785377   
4       14B02190        4  2018-04-24 22:40:59   17.0  106.696230  10.784951   
...          ...      ...                  ...    ...         ...        ...   
232445  99A20483        1  2018-04-24 18:33:30   34.0  106.686264  10.787631   
232446  99A20483        0  2018-04-24 18:33:40   42.0  106.685670  10.788170   
232447  99A20483        1  2018-04-24 18:34:00   56.0  106.684050  10.789608   
232448  99A20483        2  2018-04-24 18:34:10   50.0  106.683010  10.790563   
232449  99A20483        3  2018-04-24 18:34:20   43.0  106.681980  10.791529   

           heading  vehicleType  time_interval    distance  heading_interval  \
0       226.266560          100           20.0   11.221452          0.000000   
1       224.953206          100           10.0   64.213887          1.313354   
2       222.701121          100           30.0  110.879986          2.252085   
3       221.411063          100           10.0   62.981940          1.290059   
4       224.228675          100           40.0  109.985633          2.817612   
...            ...          ...            ...         ...               ...   
232445  312.544653          300           10.0   88.328078          0.919441   
232446  311.917285          300           20.0  238.494239          0.627368   
232447  312.884703          300           10.0  155.502930          0.967418   
232448  313.488455          300           10.0  155.548641          0.603752   
232449  313.488455          300            0.0    0.000000          0.000000   

        id_color  
0           3430  
1           3430  
2           3430  
3           3430  
4           3430  
...          ...  
232445      1204  
232446      1204  
232447      1204  
232448      1204  
232449      1204  

[232450 rows x 12 columns]

In [13]:
df_vehicle_count

index  vehicle    id
0      51F33308      494     0
1      51G48323      472     1
2      51G50101      438     2
3      51C31679      404     3
4      51F85909      400     4
...         ...      ...   ...
5851   51B18551        5  5851
5852   80M00242        5  5852
5853   51C57019        4  5853
5854   51C59948        3  5854
5855  50LD00479        3  5855

[5856 rows x 3 columns]

In [14]:
# colors = ['#e6194b', '#3cb44b', '#ffe119', '#4363d8', '#f58231', '#911eb4',
#         '#46f0f0', '#f032e6', '#bcf60c', '#fabebe', '#008080', '#e6beff', 
#         '#9a6324', '#fffac8', '#707000', '#aaa0c3', '#808000', '#ffd8b1', 
#         '#000075', '#808080','#FFBF00','#9966CC','#7FFFD4']*1000
import random
colors = []

colors = ["#"+''.join([random.choice('0123456789ABCDEF') for j in range(6)])
             for i in range(len(df["vehicle"].unique()))]

In [15]:
len(colors)

5856

In [16]:
def create_map(df, colors):
    m = folium.Map(location=[df.x.mean(), df.y.mean()], zoom_start=9, tiles='Open Streetmap')
    
    for _, row in df.iterrows():
#         if row[cluster_column] == -1:
#             cluster_colour = '#000000'
#         else:
#             cluster_colour = cols[row[id]]
#         id_color = df_vehicle_count[df_vehicle_count['name']==row.vehicle]['id'].values[0]
        vehicle_colour = colors[dict_id[row.vehicle]]
        folium.CircleMarker(
        location=[row['x'],row['y']],
        radius=1,
        popup=row['vehicle'],color=vehicle_colour,
        fill=True,
        fill_colour=vehicle_colour).add_to(m)
    return m

In [17]:
list(pd.DataFrame(df["vehicle"].value_counts()[:10]).index)

['51F33308',
 '51G48323',
 '51G50101',
 '51C31679',
 '51F85909',
 '51F89385',
 '51F34250',
 '51F37548',
 '51F85359',
 '51F65770']

## MINH HỌA CÁC ĐIỂM DI CHUYỂN CỦA 5 XE CÓ NHIỀU ĐIỂM NHẤT TRÊN BẢN ĐỒ

In [18]:
%%time
create_map(df.loc[df['vehicle'].isin(list(pd.DataFrame(df["vehicle"].value_counts()[:5]).index))], colors)

Wall time: 593 ms


## MINH HỌA CÁC ĐIỂM DI CHUYỂN CỦA 5 XE NHIỀU ĐIỂM NHẤT SAU KHI ÁNH XẠ VÀO CÁC ID NODE

In [19]:
df_node = pd.read_csv("osm_node.csv")

In [20]:
df_node

id        lat         lon  version                  timestamp  \
0       1419383  10.788461  106.664307        1  2020-11-30 03:20:07+00:00   
1       1419404  10.789730  106.664316        1  2020-11-30 03:20:07+00:00   
2       1419414  10.787892  106.664322        1  2020-11-30 03:20:07+00:00   
3       1419415  10.766674  106.664324        1  2020-11-30 03:20:07+00:00   
4       1419423  10.792145  106.664329        1  2020-11-30 03:20:07+00:00   
...         ...        ...         ...      ...                        ...   
20012  13599586  10.771815  106.697815        1  2020-11-30 03:20:07+00:00   
20013  13608426  10.777344  106.679361        1  2020-11-30 03:20:07+00:00   
20014  13608427  10.777360  106.679392        1  2020-11-30 03:20:07+00:00   
20015  13608428  10.777361  106.679430        1  2020-11-30 03:20:07+00:00   
20016  13608429  10.777346  106.679458        1  2020-11-30 03:20:07+00:00   

       changeset  uid       user vbd:layer  
0              1    1  vietbando   vbdroad  
1              1    1  vietbando   vbdroad  
2              1    1  vietbando   vbdroad  
3              1    1  vietbando   vbdroad  
4              1    1  vietbando   vbdroad  
...          ...  ...        ...       ...  
20012          1    1  vietbando   vbdroad  
20013          1    1  vietbando   vbdroad  
20014          1    1  vietbando   vbdroad  
20015          1    1  vietbando   vbdroad  
20016          1    1  vietbando   vbdroad  

[20017 rows x 9 columns]

In [21]:
df_way = pd.read_csv("osm_way.csv")

In [22]:
df_way

id  version                  timestamp  changeset  uid       user  \
0      2560080        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
1      2560095        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
2      2560109        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
3      2560113        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
4      2560189        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
...        ...      ...                        ...        ...  ...        ...   
10883  2714244        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
10884  2714245        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
10885  2719553        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
10886  2719554        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
10887  2719555        1  2020-11-30 03:20:07+00:00          1    1  vietbando   

                                                     ref vbd:layer  \
0                                     [1451209, 1450777]   vbdroad   
1       [1453773, 13416279, 13416280, 13416281, 1453627]   vbdroad   
2      [1453097, 13416288, 13416289, 13416290, 134162...   vbdroad   
3                           [1452755, 13416307, 1453223]   vbdroad   
4                                     [1451462, 1452079]   vbdroad   
...                                                  ...       ...   
10883                       [1481237, 13599586, 1480757]   vbdroad   
10884                                 [1481237, 1482113]   vbdroad   
10885                                 [1446056, 1446927]   vbdroad   
10886  [1446927, 13608426, 13608427, 13608428, 136084...   vbdroad   
10887                                 [1446927, 1447586]   vbdroad   

                vbd:namebase  vbd:type  vbd:vtunnel  \
0                  Cao Thắng         3            0   
1        105 Đường Cao Thắng         5            0   
2        105 Đường Cao Thắng         5            0   
3        129 Đường Cao Thắng         5            0   
4      Cư Xá Nguyễn Văn Trỗi         3            0   
...                      ...       ...          ...   
10883         Phan Chu Trinh         3            0   
10884                 Lê Lai         3            0   
10885                   Số 8         3            0   
10886                   Số 8         3            0   
10887                    NaN         0            0   

                              name  vbd:voverpass  vbd:level      highway  
0                  Đường Cao Thắng              0          2    secondary  
1          Hẻm 105 Đường Cao Thắng              0          3  residential  
2          Hẻm 105 Đường Cao Thắng              0          3  residential  
3          Hẻm 129 Đường Cao Thắng              0          3  residential  
4      Đường Cư Xá Nguyễn Văn Trỗi              0          2    secondary  
...                            ...            ...        ...          ...  
10883         Đường Phan Chu Trinh              0          2    secondary  
10884                 Đường Lê Lai              0          1      primary  
10885                   Đường Số 8              0          2    secondary  
10886                   Đường Số 8              0          2    secondary  
10887                          NaN              0          2    secondary  

[10888 rows x 15 columns]

In [23]:
def add_markers_df_node_df_vehicle(df_node, df_vehicle, colors):
    df_vehicle_count = pd.DataFrame(df_vehicle["vehicle"].value_counts())
    df_vehicle_count = df_vehicle_count.reset_index()
    df_vehicle_count = df_vehicle_count.rename(columns = {'index':'name'})
    df_vehicle_count['id'] = df_vehicle_count.index
    m = folium.Map(location=[df_vehicle.x.mean(), df_vehicle.y.mean()], zoom_start=9, tiles='MapQuest Open Aerial')
    
    for _, row in df_vehicle.iterrows():
#         if row[cluster_column] == -1:
#             cluster_colour = '#000000'
#         else:
#             cluster_colour = cols[row[id]]
        id_color = df_vehicle_count[df_vehicle_count['name']==row.vehicle]['id'].values[0]
        vehicle_colour = colors[id_color]
        folium.CircleMarker(
        location=[row['x'],row['y']],
        radius=5,
        popup=row['vehicle'],color=vehicle_colour,
        fill=True,
        fill_colour=vehicle_colour).add_to(m)
    coords = []
    for i, row in df_node.iterrows():
        coords.append([row.lat, row.lon])
    for coord in coords:
        folium.CircleMarker(location = coord,
                            radius = 1, 
                            fill = True,
                            fill_color = '#F50057',
                            fill_opacity = 0.75,
                            color = 'whitesmoke',
                            weight = 0.5).add_to(m)
    return m

### DỮ LIỆU 5 XE CÓ NHIỀU ĐIỂM DI CHUYỂN NHẤT

In [24]:
df_first_5_the_most_vehicle = df.loc[df['vehicle'].isin(list(pd.DataFrame(df["vehicle"].value_counts()[:5]).index))]

### DỮ LIỆU CÁC NODE VÀ WAY MÀ TẤT CẢ CÁC XE ĐI QUA

In [26]:
df_list_way_vehicle = pd.read_csv("list_way_vehicle_2.csv")

In [27]:
df_list_way_vehicle

51G41457  \
0  ['1478296', '1478186', '1477370', '1475403', '...   
1  [2586261, 2586247, 2582911, 2582909, 2588008, ...   

                                             68H6454  \
0  ['1421369', '1428943', '1435040', '1437395', '...   
1  [2620052, 2620044, 2621828, 2685948, 2617573, ...   

                                            51B07982  \
0  ['1478203', '1476248', '1470784', '1456175', '...   
1               [2587943, 2682640, 2588695, 2588696]   

                                            51D15657  \
0  ['1481201', '1480815', '1480000', '1479589', '...   
1  [2680848, 2588912, 2588916, 2588918, 2590185, ...   

                                            86A01639  \
0  ['1421496', '1421809', '1421230', '1419734', '...   
1  [2688030, 2612733, 2590060, 2591281, 2588036, ...   

                                           51F77061A  \
0  ['1420021', '1423184', '1421724', '1422532', '...   
1  [2665593, 2620501, 2620482, 2613110, 2622636, ...   

                                            51G49993  \
0  ['1480646', '13559018', '1480000', '1477018', ...   
1  [2680850, 2590166, 2590857, 2588795, 2620814, ...   

                                            51D16144  \
0  ['1452845', '1460166', '1462652', '1465084', '...   
1  [2589673, 2589607, 2587072, 2587999, 2586472, ...   

                                            51B21840  \
0  ['1473995', '1470572', '1467944', '1467760', '...   
1  [2589437, 2589490, 2590868, 2590871, 2589534, ...   

                                            51F96429  ...  \
0  ['1461395', '1466461', '1468331', '1470137', '...  ...   
1               [2590864, 2590869, 2588798, 2572818]  ...   

                                            51F78158  \
0  ['1465686', '13448737', '1464608', '1465115', ...   
1  [2632617, 2588299, 2586019, 2586017, 2586015, ...   

                                            51B01358  \
0  ['1478078', '1464585', '1462759', '1461293', '...   
1  [2682072, 2588760, 2613482, 2614756, 2614758, ...   

                                            51B20999  \
0  ['1473995', '1469021', '1476415', '1476508', '...   
1  [2589558, 2586459, 2586478, 2586400, 2582902, ...   

                                            51F77061  \
0  ['1420021', '1421295', '1421770', '1423184', '...   
1  [2665579, 2665588, 2665593, 2665594, 2665596, ...   

                                            60B03895  \
0  ['1478064', '1477018', '1476248', '1474835', '...   
1  [2588912, 2588916, 2590172, 2590158, 2590857, ...   

                                            30A12670  \
0  ['1478186', '1477370', '1476111', '1474434', '...   
1  [2586247, 2586210, 2582909, 2582911, 2588005, ...   

                                            79A12947  \
0  ['1469192', '1468098', '1466982', '1466035', '...   
1  [2587960, 2587959, 2572731, 2572730, 2572729, ...   

                                            51G46873  \
0  ['1421654', '1421840', '1421751', '1423956', '...   
1  [2574542, 2667963, 2614376, 2620046, 2622296, ...   

                                            51C81075  \
0  ['1476415', '1475078', '1473977', '1474590', '...   
1  [2590149, 2590599, 2590858, 2587954, 2588780, ...   

                                            51B40283  
0  ['1476711', '1472117', '1471511', '1474590', '...  
1  [2590155, 2590857, 2590599, 2586021, 2586020, ...  

[2 rows x 5856 columns]

In [28]:
df_first_5_the_most_vehicle['vehicle'].unique()

array(['51C31679', '51F33308', '51F85909', '51G48323', '51G50101'],
      dtype=object)

In [29]:
df_list_way_vehicle_the_most_5_vehicle = df_list_way_vehicle[list(df_first_5_the_most_vehicle['vehicle'].unique())]

### DỮ LIỆU CÁC NODE VÀ WAY MÀ 5 XE ĐI QUA

In [30]:
df_list_way_vehicle_the_most_5_vehicle

51C31679  \
0  ['1427819', '1429053', '1429381', '1430646', '...   
1  [2611821, 2611822, 2614418, 2614419, 2614420, ...   

                                            51F33308  \
0  ['1481237', '1479407', '1477529', '1479277', '...   
1  [2714243, 2582907, 2582908, 2582964, 2586325, ...   

                                            51F85909  \
0  ['1479970', '1478617', '1478335', '1475866', '...   
1  [2582861, 2582862, 2582863, 2586474, 2681572, ...   

                                            51G48323  \
0  ['1439326', '1438579', '1438387', '13479538', ...   
1  [2618045, 2611867, 2611868, 2618102, 2618107, ...   

                                            51G50101  
0  ['1479688', '1477482', '1477299', '1476990', '...  
1  [2586252, 2586243, 2586355, 2586356, 2586358, ...

In [31]:
df_list_way_vehicle_the_most_5_vehicle = df_list_way_vehicle_the_most_5_vehicle.transpose()

In [32]:
for i in df_list_way_vehicle_the_most_5_vehicle.columns:
    df_list_way_vehicle_the_most_5_vehicle[i] = df_list_way_vehicle_the_most_5_vehicle[i].str.replace("'",'')
    df_list_way_vehicle_the_most_5_vehicle[i] = df_list_way_vehicle_the_most_5_vehicle[i].str.replace(" ",'')
    df_list_way_vehicle_the_most_5_vehicle[i] = df_list_way_vehicle_the_most_5_vehicle[i].str.replace("]",'')
    df_list_way_vehicle_the_most_5_vehicle[i] = df_list_way_vehicle_the_most_5_vehicle[i].str.replace("[",'')
    df_list_way_vehicle_the_most_5_vehicle[i] = df_list_way_vehicle_the_most_5_vehicle[i].str.split(',')

In [33]:
df_list_way_vehicle_the_most_5_vehicle

0  \
51C31679  [1427819, 1429053, 1429381, 1430646, 1431125, ...   
51F33308  [1481237, 1479407, 1477529, 1479277, 1475679, ...   
51F85909  [1479970, 1478617, 1478335, 1475866, 1471291, ...   
51G48323  [1439326, 1438579, 1438387, 13479538, 1437958,...   
51G50101  [1479688, 1477482, 1477299, 1476990, 1476776, ...   

                                                          1  
51C31679  [2611821, 2611822, 2614418, 2614419, 2614420, ...  
51F33308  [2714243, 2582907, 2582908, 2582964, 2586325, ...  
51F85909  [2582861, 2582862, 2582863, 2586474, 2681572, ...  
51G48323  [2618045, 2611867, 2611868, 2618102, 2618107, ...  
51G50101  [2586252, 2586243, 2586355, 2586356, 2586358, ...

In [34]:
df_list_way_vehicle_the_most_5_vehicle[0].loc['51C31679'][0]

'1427819'

In [35]:
df_node_the_most_5_vehicle = pd.DataFrame()
for vehicle in df_first_5_the_most_vehicle['vehicle'].unique():
    list_node_vehicle = df_list_way_vehicle_the_most_5_vehicle[0].loc[vehicle]
    df_node_vehicle = df_node[df_node['id'].isin(list_node_vehicle)]
    df_node_vehicle['vehicle'] = vehicle
    df_node_the_most_5_vehicle = df_node_the_most_5_vehicle.append(df_node_vehicle)

In [36]:
df_node_the_most_5_vehicle

id        lat         lon  version                  timestamp  \
724     1425936  10.785123  106.667999        1  2020-11-30 03:20:07+00:00   
807     1426505  10.784946  106.668328        1  2020-11-30 03:20:07+00:00   
835     1426691  10.784893  106.668426        1  2020-11-30 03:20:07+00:00   
900     1427169  10.784738  106.668718        1  2020-11-30 03:20:07+00:00   
993     1427819  10.784531  106.669109        1  2020-11-30 03:20:07+00:00   
...         ...        ...         ...      ...                        ...   
17773  13556884  10.775567  106.680090        1  2020-11-30 03:20:07+00:00   
17774  13556885  10.777456  106.681162        1  2020-11-30 03:20:07+00:00   
18319  13560327  10.785910  106.684722        1  2020-11-30 03:20:07+00:00   
18685  13560826  10.781602  106.678507        1  2020-11-30 03:20:07+00:00   
18688  13560829  10.781818  106.678502        1  2020-11-30 03:20:07+00:00   

       changeset  uid       user vbd:layer   vehicle  
724            1    1  vietbando   vbdroad  51C31679  
807            1    1  vietbando   vbdroad  51C31679  
835            1    1  vietbando   vbdroad  51C31679  
900            1    1  vietbando   vbdroad  51C31679  
993            1    1  vietbando   vbdroad  51C31679  
...          ...  ...        ...       ...       ...  
17773          1    1  vietbando   vbdroad  51G50101  
17774          1    1  vietbando   vbdroad  51G50101  
18319          1    1  vietbando   vbdroad  51G50101  
18685          1    1  vietbando   vbdroad  51G50101  
18688          1    1  vietbando   vbdroad  51G50101  

[1112 rows x 10 columns]

### MINH HỌA CÁC NODE CỦA 5 XE ĐI QUA TRÊN BẢN ĐỒ

Các node là các điểm giao nhau giữa 2 đường hoặc các điểm phân chia đường thành đường gấp khúc.

In [37]:
def create_map_1(df, colors):
    m = folium.Map(location=[df.lat.mean(), df.lon.mean()], zoom_start=9, tiles='Open Streetmap')
    
    for _, row in df.iterrows():
#         if row[cluster_column] == -1:
#             cluster_colour = '#000000'
#         else:
#             cluster_colour = cols[row[id]]
#         id_color = df_vehicle_count[df_vehicle_count['name']==row.vehicle]['id'].values[0]
        vehicle_colour = colors[dict_id[row.vehicle]]
        folium.CircleMarker(
        location=[row['lat'],row['lon']],
        radius=1,
        popup=row['vehicle'],color=vehicle_colour,
        fill=True,
        fill_colour=vehicle_colour).add_to(m)
    return m

In [38]:
create_map_1(df_node_the_most_5_vehicle, colors)

## MINH HỌA CÁC ĐIỂM DI CHUYỂN CỦA 5 XE NHIỀU ĐIỂM NHẤT SAU KHI ÁNH XẠ VÀO CÁC ID WAY BẰNG CÁCH TÌM CÁC NODE TRÊN CHÍNH CÁC WAY ĐÓ

In [39]:
df_way_the_most_5_vehicle = pd.DataFrame()
for vehicle in df_first_5_the_most_vehicle['vehicle'].unique():
    list_way_vehicle = df_list_way_vehicle_the_most_5_vehicle[1].loc[vehicle]
    df_way_vehicle = df_way[df_way['id'].isin(list_way_vehicle)]
    df_way_vehicle['vehicle'] = vehicle
    df_way_the_most_5_vehicle = df_way_the_most_5_vehicle.append(df_way_vehicle)

In [40]:
df_way_the_most_5_vehicle['ref'] = df_way_the_most_5_vehicle['ref'].str.replace("[","")
df_way_the_most_5_vehicle['ref'] = df_way_the_most_5_vehicle['ref'].str.replace("]","")
df_way_the_most_5_vehicle['ref'] = df_way_the_most_5_vehicle['ref'].str.replace(" ","")
df_way_the_most_5_vehicle['ref'] = df_way_the_most_5_vehicle['ref'].str.split(',')

In [41]:
df_way_the_most_5_vehicle['ref']

138                                     [1460365, 1460997]
139                                     [1460997, 1462038]
140                                     [1461665, 1462566]
141                                     [1462566, 1463769]
142                                     [1463769, 1464809]
                               ...                        
9687     [1445570, 13560826, 13560827, 13560828, 135608...
9688                          [1445939, 13560830, 1446353]
9689                          [1451151, 13560831, 1450260]
9849                                    [1450776, 1450450]
10642                                   [1448465, 1447890]
Name: ref, Length: 839, dtype: object

In [42]:
df_way_the_most_5_vehicle = df_way_the_most_5_vehicle.explode('ref')

In [43]:
df_way_the_most_5_vehicle

id  version                  timestamp  changeset  uid       user  \
138    2572725        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
138    2572725        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
139    2572726        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
139    2572726        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
140    2572727        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
...        ...      ...                        ...        ...  ...        ...   
9689   2682531        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
9849   2682704        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
9849   2682704        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
10642  2686718        1  2020-11-30 03:20:07+00:00          1    1  vietbando   
10642  2686718        1  2020-11-30 03:20:07+00:00          1    1  vietbando   

           ref vbd:layer        vbd:namebase  vbd:type  vbd:vtunnel  \
138    1460365   vbdroad        Nguyễn Thông         3            0   
138    1460997   vbdroad        Nguyễn Thông         3            0   
139    1460997   vbdroad        Nguyễn Thông         3            0   
139    1462038   vbdroad        Nguyễn Thông         3            0   
140    1461665   vbdroad   Nguyễn Đình Chiểu         3            0   
...        ...       ...                 ...       ...          ...   
9689   1450260   vbdroad  Nguyễn Phúc Nguyên         3            0   
9849   1450776   vbdroad             Kỳ Đồng         3            0   
9849   1450450   vbdroad             Kỳ Đồng         3            0   
10642  1448465   vbdroad                Số 2         3            0   
10642  1447890   vbdroad                Số 2         3            0   

                           name  vbd:voverpass  vbd:level    highway   vehicle  
138          Đường Nguyễn Thông              0          2  secondary  51C31679  
138          Đường Nguyễn Thông              0          2  secondary  51C31679  
139          Đường Nguyễn Thông              0          2  secondary  51C31679  
139          Đường Nguyễn Thông              0          2  secondary  51C31679  
140     Đường Nguyễn Đình Chiểu              0          1    primary  51C31679  
...                         ...            ...        ...        ...       ...  
9689   Đường Nguyễn Phúc Nguyên              0          2  secondary  51G50101  
9849              Đường Kỳ Đồng              0          2  secondary  51G50101  
9849              Đường Kỳ Đồng              0          2  secondary  51G50101  
10642                Đường Số 2              0          2  secondary  51G50101  
10642                Đường Số 2              0          2  secondary  51G50101  

[2200 rows x 16 columns]

In [44]:
df_node_from_df_way_5_vehicle = pd.DataFrame()
for vehicle in df_first_5_the_most_vehicle['vehicle'].unique():
    df_way_temp = df_way_the_most_5_vehicle[df_way_the_most_5_vehicle['vehicle']==vehicle]
    df_node_temp = df_node[df_node['id'].isin(list(df_way_temp['ref']))]
    df_node_temp['vehicle'] = vehicle
    df_node_from_df_way_5_vehicle = df_node_from_df_way_5_vehicle.append(df_node_temp)
df_node_from_df_way_5_vehicle

id        lat         lon  version                  timestamp  \
688     1425670  10.785203  106.667843        1  2020-11-30 03:20:07+00:00   
724     1425936  10.785123  106.667999        1  2020-11-30 03:20:07+00:00   
774     1426266  10.785015  106.668200        1  2020-11-30 03:20:07+00:00   
807     1426505  10.784946  106.668328        1  2020-11-30 03:20:07+00:00   
835     1426691  10.784893  106.668426        1  2020-11-30 03:20:07+00:00   
...         ...        ...         ...      ...                        ...   
18686  13560827  10.781725  106.678469        1  2020-11-30 03:20:07+00:00   
18687  13560828  10.781757  106.678468        1  2020-11-30 03:20:07+00:00   
18688  13560829  10.781818  106.678502        1  2020-11-30 03:20:07+00:00   
18689  13560830  10.782043  106.678891        1  2020-11-30 03:20:07+00:00   
18690  13560831  10.778508  106.681226        1  2020-11-30 03:20:07+00:00   

       changeset  uid       user vbd:layer   vehicle  
688            1    1  vietbando   vbdroad  51C31679  
724            1    1  vietbando   vbdroad  51C31679  
774            1    1  vietbando   vbdroad  51C31679  
807            1    1  vietbando   vbdroad  51C31679  
835            1    1  vietbando   vbdroad  51C31679  
...          ...  ...        ...       ...       ...  
18686          1    1  vietbando   vbdroad  51G50101  
18687          1    1  vietbando   vbdroad  51G50101  
18688          1    1  vietbando   vbdroad  51G50101  
18689          1    1  vietbando   vbdroad  51G50101  
18690          1    1  vietbando   vbdroad  51G50101  

[1684 rows x 10 columns]

In [45]:
create_map_1(df_node_from_df_way_5_vehicle, colors)